In [1]:
# 1).EPS growth 1-year change (%) = over 20%.                done
# 2) EPS growth quarter over quarter = over 20%.             done
# 3) Sales/revenue growth quarter over quarter = over 20%.   done
# 4) EPS Next Year change (Estimate %) (forecast) = over 15% done
# 5) Institutional Ownership = over 30%.                     done
# 6) Price is over $15                                       done
# 7) EPS growth 3-year avg (%) = over 15%                    done
# 8) Sales growth 3-year avg (%) = over 15%                  done

In [2]:
import json
import requests
import numpy as np
import time 

fhkey ="bt3efpf48v6tfcs816eg"
apiKey = '8a1cf9d14d53126b05c8a7636fe3d006'

try:
    # For Python 3.0 and later
        from urllib.request import urlopen
except ImportError:
# Fall back to Python 2's urllib2
    from urllib2 import urlopen

In [3]:
def getData(url,symbol="none"):
    """
    Receive the content of ``url``, parse it as JSON and return the object.

    Parameters
    ----------
    url : str
    symbol : str
    
    Returns
    -------
    dict
    """
    if (symbol == "none"):
        response = urlopen(url)
    else:
        response = urlopen(url % symbol)

    data = response.read().decode("utf-8")
    return json.loads(data)

In [4]:
def allInOne(symbol):
    annualGrowth = getData(f"https://financialmodelingprep.com/api/v3/income-statement-growth/{symbol}?limit=3&apikey={apiKey}")
    quarterGrowth = getData(f"https://financialmodelingprep.com/api/v3/financial-growth/{symbol}?period=quarter&limit=1&apikey={apiKey}")
    quote = getData(f"https://financialmodelingprep.com/api/v3/quote/{symbol}?apikey={apiKey}")
    institutionalHolders = getData(f"https://financialmodelingprep.com/api/v3/institutional-holder/{symbol}?apikey={apiKey}")
    estimate = requests.get(f"https://finnhub.io/api/v1/stock/earnings?symbol={symbol}&token={fhkey}").json()                
    
    #1 year eps growth
    
    oneYearEpsGrowth = annualGrowth[0]["growthEPS"]  
    
    #quarter eps and revenue growth
    
    quarterEpsGrowth = quarterGrowth[0]["epsgrowth"]     
    quarterRevGrowth = quarterGrowth[0]["revenueGrowth"] 
    
    #next year growth
    
    forecastGrowth = estimate[0]["estimate"]
    currentEps = quote[0]["eps"]
    if forecastGrowth is None:
        forecastGrowth = 0
    else:
        forecastGrowth = (forecastGrowth-currentEps)/currentEps
    
    #institutional ownership
    
    totalShares = quote[0]["sharesOutstanding"]
    ownership = 0
    institutionalShares = 0
    for i in institutionalHolders:
        institutionalShares += i["shares"]
    ownership = institutionalShares/totalShares
        
    #price
    
    price = quote[0]["price"]
    
    #3 year average eps and revenue growth
        
    epsAvg3yGrowth = 0
    revAvg3yGrowth = 0                
    for i in annualGrowth:                         
        epsAvg3yGrowth += i["growthEPS"]             
        revAvg3yGrowth += i["growthRevenue"]         
    epsAvg3yGrowth /= 3                              
    revAvg3yGrowth /= 3  
    
    return (oneYearEpsGrowth > .2) and (quarterEpsGrowth > .2) and (quarterRevGrowth > .2) and (forecastGrowth > .15) and (ownership > .3) and (price > 15) and (epsAvg3yGrowth > .15) and (revAvg3yGrowth > .15)

In [5]:
def getSymbols(lst):
    temp = getData(f"https://financialmodelingprep.com/api/v3/dowjones_constituent?apikey={apiKey}")
    for i in temp:
        lst.append(i["symbol"])
    temp = getData(f"https://financialmodelingprep.com/api/v3/nasdaq_constituent?apikey={apiKey}")
    for i in temp:
        if (i["symbol"] not in lst):
            lst.append(i["symbol"])
    temp = getData(f"https://financialmodelingprep.com/api/v3/sp500_constituent?apikey={apiKey}")
    for i in temp:
        if (i["symbol"] not in lst):
            lst.append(i["symbol"])

In [6]:
lst = []
getSymbols(lst)
passed = {"tickers": []}

n= 10 # number of groups

groups = np.array_split(lst, n)

for symbol in groups:
    for i in symbol:
        if (allInOne(i)):
            passed["tickers"].append(i)


    time.sleep(60)

print(passed)

{'tickers': ['MRNA']}
